# Problem Statement

At https://archive.ics.uci.edu/ml/machine-learning-databases/housing/housing.data, you will find the famous Boston Housing dataset. This consists of 506 data items. You will find the explanation of the dataset at https://archive.ics.uci.edu/ml/machine-learning-databases/housing/housing.names. Each is 13 measurements, and a house price. The data was collected by Harrison, D. and Rubinfeld, D.L in the 1970s (a date which explains the very low house prices). The dataset has been widely used in regression exercises, but seems to be waning in popularity. At least one of the independent variables measures the fraction of population nearby that is ''Black'' (their word, not mine). This variable appears to have had a significant effect on house prices then (and, sadly, may still now).

 Regress house price (variable 14) against all others, and use leverage, Cook's distance, and standardized residuals to find possible outliers. Use plot(your_linear_regression_model) to produce a diagnostic plot that allows you to identify possible outliers (points with high residual or high leverage or high influence). Give the indices of possible outliers and explain why you think they are outliers. The reason being an outlier may not be same, so please be sure you understand the plot well. (You can read R tutorial provided above if you have any questions).

 Remove all points you suspect as outliers, and compute a new regression. Reproduce a diagnostic plot that allows you to identify possible outliers. We do not require explanations this time.

 Apply a Box-Cox transformation (use boxcox command) to the dependent variable, what is the best value of the parameter?

 Now transform the dependent variable, build a linear regression, and check the standardized residuals. If they look acceptable, produce a plot of fitted house price against true house price.

In [5]:
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"

In [7]:
fit = lm(price ~ . -price, housing)
plot(fit)

The Residuals vs Fitted graph appears to have a soft U-shape tendency, it seems to have some non-linear pattern.
In the Normal Q-Q plot, the relationship between predictors and response mostly has a linear trend with a little deviation.
In Scale Location plot, there is a soft U-shaped tendency in the plot instead of a horizontal line.
In Residuals vs Leverage plot, the points we should be looking for are values in the upper right or lower right corners, which are outside the red dashed Cook’s distance line. These are points that would be influential in the model and removing them would likely noticeably alter the regression results. But the plot doesn’t show any influential cases as all of the cases are within the the dashed Cook’s distance line.
Possible outliers from the plots:  365, 369, 372, 373 

In [8]:
#Cross checking with outlierTest() package from 'car' library
library("car")
outlierTest(fit)

    rstudent unadjusted p-value Bonferonni p
369 5.907411         6.4998e-09   3.2889e-06
372 5.491079         6.4185e-08   3.2478e-05
373 5.322247         1.5617e-07   7.9020e-05

In [18]:
#removing outlier points 365, 369, 372, 373 from last iteration and fitting the linear model
housing = housing[-c(365, 369, 372, 373),]
fit = lm(price ~ . -price, housing)
plot(fit)

Possible outliers from the above plots: 366, 368, 370, 371

In [19]:
#Cross checking with outlierTest() package from 'car' library
library("car")
outlierTest(fit)

    rstudent unadjusted p-value Bonferonni p
370 4.831620         1.8174e-06   0.00091235
366 4.479314         9.3401e-06   0.00468880
371 4.268428         2.3669e-05   0.01188200
413 4.110835         4.6264e-05   0.02322400
368 4.004975         7.1710e-05   0.03599800

In [20]:
#removing outlier points 366, 368, 370, 371, 413 from last iteration and fitting the linear model
housing = housing[-c(366, 368, 370, 371, 413),]
fit = lm(price ~ . -price, housing)
plot(fit)

In [22]:
#Cross checking with outlierTest() package from 'car' library
library("car")
outlierTest(fit)

    rstudent unadjusted p-value Bonferonni p
366 5.110607         4.6376e-07   0.00023049
371 4.789421         2.2296e-06   0.00110810
368 4.465313         9.9685e-06   0.00495430
413 4.370171         1.5215e-05   0.00756200

So with the above iterations we found the below list of possible outliers:
365, 369, 372, 373, 366, 368, 370, 371, 413

In [28]:
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
housing = housing[-c(365, 369, 372, 373, 366, 368, 370, 371, 413),]
fit = lm(price ~ . -price, housing)
plot(fit)

In [29]:
#Cross checking with outlierTest() package from 'car' library
library("car")
outlierTest(fit)


No Studentized residuals with Bonferonni p < 0.05
Largest |rstudent|:
    rstudent unadjusted p-value Bonferonni p
375 3.850358         0.00013385     0.066525

Possible outliers: 162, 375, 381

In [30]:
#removing all possible outliers in one set (162, 365, 366, 368, 369, 370, 372, 371, 373, 375, 381, 413)
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
housing = housing[-c(162, 365, 366, 368, 369, 370, 372, 371, 373, 375, 381, 413),]
fit = lm(price ~ . -price, housing)
plot(fit)

In [39]:
########################## Outlier detection by cooks distance -- condition: 4/sample_size
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
fit = lm(price ~ . -price, housing)
cooksd <- cooks.distance(fit)
sample_size <- nrow(housing)
plot(cooksd, pch="*", cex=2, main="Influential Observations by Cooks distance") # plot cook's distance
abline(h = 4/sample_size, col="red")
#abline(h = 4*mean(cooksd, na.rm=T), col="red")
text(x=1:length(cooksd)+1, y=cooksd, labels=ifelse(cooksd>4/sample_size, names(cooksd),""), col="red")  # add labels
#text(x=1:length(cooksd)+1, y=cooksd, labels=ifelse(cooksd>4*mean(cooksd, na.rm=T), names(cooksd),""), col="red")  # add labels
#influential <- as.numeric(names(cooksd)[(cooksd > (4*mean(cooksd, na.rm=T)))])
influential <- as.numeric(names(cooksd)[(cooksd > (4/sample_size))])
influential

[1]  65 142 149 162 163 164 167 187 196 205 215 226 229 234 254 263 268 365 366
[20] 368 369 370 371 372 373 375 376 381 413 415

In [45]:
########################## Outlier detection by cooks distance -- condition: 4*mean(cooksd, na.rm=T)
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
fit = lm(price ~ . -price, housing)
cooksd <- cooks.distance(fit)
sample_size <- nrow(housing)
plot(cooksd, pch="*", cex=2, main="Influential Observations by Cooks distance") # plot cook's distance
abline(h = 4/sample_size, col="red")
#abline(h = 4*mean(cooksd, na.rm=T), col="red")
#text(x=1:length(cooksd)+1, y=cooksd, labels=ifelse(cooksd>4/sample_size, names(cooksd),""), col="red")  # add labels
text(x=1:length(cooksd)+1, y=cooksd, labels=ifelse(cooksd>4*mean(cooksd, na.rm=T), names(cooksd),""), col="red")  # add labels
influential2 <- as.numeric(names(cooksd)[(cooksd > (4*mean(cooksd, na.rm=T)))])
#influential <- as.numeric(names(cooksd)[(cooksd > (4/sample_size))])
influential2

[1]  65 142 162 163 164 167 187 215 226 229 254 365 366 368 369 370 371 372 373
[20] 375 381 413 415

In [46]:
######################## Outlier detection by using leverage 
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
fit = lm(price ~ . -price, housing)
lev <- hatvalues(fit)
sample_size <- nrow(housing)
plot(lev, pch="*", cex=2, main="Influential Observation by leverage") # plot leverage
abline(h = 0.1, col="red")
text(x=1:length(lev)+1, y=lev, labels=ifelse(lev>0.1, names(lev),""), col="red")  # add labels
influential3 <- as.numeric(names(lev)[(lev > 0.1)])
influential3

[1] 381 406 411 419

In [54]:
#removing outliers based on cook's distance with threshold = 4*mean(cooksd, na.rm=T) 
housing = read.table("housing.data")
colnames(housing)[colnames(housing)=="V14"] <- "price"
housing = housing[-influential2,]
fit = lm(price ~ . -price, housing)
plot(fit)

In [55]:
#########################Apply boxcox
library(MASS)
bc = boxcox(price ~ . -price, data = housing)
lambda = with(bc, x[which.max(y)])

In [56]:
housing['price'] = (housing['price']^lambda -1)/lambda
fit = lm(price ~ . -price, housing)
plot(fit)
plot((predict(fit) * lambda+1)^(1/lambda), t((housing['price'] * lambda+1)^(1/lambda)), xlab="predicted",ylab="actual")
abline(a=0, b=1)

[1] 502